In [34]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
from scipy.stats import f_oneway
from sklearn.metrics import mean_absolute_error 
import altair as alt

In [35]:
df = pd.read_csv('StudentPerformanceFactors.csv')

In [36]:
df = df.dropna() 

df = df[df['Tutoring_Sessions'] != 8]

In [37]:
sum_stats = df['Exam_Score'].describe() 

lower_bound = sum_stats['mean'] - 3 * sum_stats['std']
upper_bound = sum_stats['mean'] + 3 * sum_stats['std'] 
filtered_df = df[(df['Exam_Score'] > lower_bound) & (df['Exam_Score'] < upper_bound)] 

In [38]:
df = df.iloc[:5000]

In [39]:
categorical_columns = ['Parental_Involvement', 'Access_to_Resources', 'Extracurricular_Activities', 'Motivation_Level', 'Internet_Access', 'Family_Income', 'Teacher_Quality', 'School_Type', 'Peer_Influence', 'Learning_Disabilities', 'Parental_Education_Level', 'Distance_from_Home', 'Gender']

In [40]:
df

Hours_Studied  Attendance Parental_Involvement Access_to_Resources  \
0                23          84                  Low                High   
1                19          64                  Low              Medium   
2                24          98               Medium              Medium   
3                29          89                  Low              Medium   
4                19          92               Medium              Medium   
...             ...         ...                  ...                 ...   
5171             12          74                  Low                High   
5172             18          84                 High                 Low   
5173             14          82               Medium              Medium   
5174             23          76               Medium              Medium   
5176             12          69                 High                High   

     Extracurricular_Activities  Sleep_Hours  Previous_Scores  \
0                            No            7               73   
1                            No            8               59   
2                           Yes            7               91   
3                           Yes            8               98   
4                           Yes            6               65   
...                         ...          ...              ...   
5171                        Yes            6               55   
5172                         No            6               64   
5173                        Yes            4               67   
5174                         No            7               66   
5176                        Yes            7               53   

     Motivation_Level Internet_Access  Tutoring_Sessions Family_Income  \
0                 Low             Yes                  0           Low   
1                 Low             Yes                  2        Medium   
2              Medium             Yes                  2        Medium   
3              Medium             Yes                  1        Medium   
4              Medium             Yes                  3        Medium   
...               ...             ...                ...           ...   
5171             High             Yes                  0        Medium   
5172           Medium             Yes                  2           Low   
5173           Medium             Yes                  1          High   
5174           Medium             Yes                  2        Medium   
5176              Low             Yes                  2           Low   

     Teacher_Quality School_Type Peer_Influence  Physical_Activity  \
0             Medium      Public       Positive                  3   
1             Medium      Public       Negative                  4   
2             Medium      Public        Neutral                  4   
3             Medium      Public       Negative                  4   
4               High      Public        Neutral                  4   
...              ...         ...            ...                ...   
5171             Low      Public       Positive                  3   
5172            High      Public       Positive                  2   
5173          Medium      Public        Neutral                  4   
5174          Medium      Public        Neutral                  3   
5176            High      Public        Neutral                  3   

     Learning_Disabilities Parental_Education_Level Distance_from_Home  \
0                       No              High School               Near   
1                       No                  College           Moderate   
2                       No             Postgraduate               Near   
3                       No              High School           Moderate   
4                       No                  College               Near   
...                    ...                      ...                ...   
5171                    No             Postgraduate             

In [41]:
slider = alt.binding_range(
    min=df['Exam_Score'].min(), 
    max=df['Exam_Score'].max(), 
    name="Exam Score", 
    step=1
)

selection = alt.selection_point(bind=slider, fields=['Exam_Score'])


chart1 = alt.Chart(df).transform_filter(
    selection
).mark_circle().encode(
    alt.X('Sleep_Hours:Q', scale=alt.Scale(domain=[4, 10]), title='Sleep Hours'),
    alt.Y('Exam_Score:Q', scale=alt.Scale(domain=[50, 101]), title='Exam Score'),
    color=alt.Color('Teacher_Quality:N', title='Teacher Quality'),
    tooltip=['Sleep_Hours', 'Exam_Score', 'Hours_Studied', 'Teacher_Quality']
).add_params(
    selection
).properties(title="Sleep Hours Vs Exam Scores Segmented by Teacher Quality")


chart2 = chart1.encode(x='Hours_Studied:Q').properties(title = \
                                                       "Hours Studied Compared To Exam Scores Labeled By Teacher Quality")

chart1 | chart2

alt.HConcatChart(...)

In [42]:
selection = alt.selection_multi(on='mouseover')


chart = alt.Chart(df).mark_circle().encode(
    x=alt.X('Attendance', scale=alt.Scale(type='linear', domain=[60, 100])),
    y=alt.Y('Exam_Score', scale=alt.Scale(type='linear', domain=[50, 105]),  title="Exam Scores"), 
    color=alt.condition(selection, 'Access_to_Resources', alt.value('lightgray'), title="Access To Resources"),
    size=alt.value(100),
    tooltip=['Attendance', 'Exam_Score', 'Access_to_Resources', 'Family_Income']
).add_selection(
    selection
)



C:\Users\sunit\AppData\Local\Temp\ipykernel_22008\1167229257.py:1: AltairDeprecationWarning: Deprecated in `altair=5.0.0`. Use selection_point instead.
  selection = alt.selection_multi(on='mouseover')
C:\Users\sunit\AppData\Local\Temp\ipykernel_22008\1167229257.py:10: AltairDeprecationWarning: Deprecated in `altair=5.0.0`. Use add_params instead.
  ).add_selection(


In [43]:
access_to_resources = ['High', 'Medium', 'Low'] 


rating_res = alt.binding_radio(
    options=access_to_resources, 
    name="Access to Resources"
)


rating_select = alt.selection_point(
    fields=['Access_to_Resources'], 
    bind=rating_res
)


rating_color_condition = alt.condition(
    rating_select,
    alt.Color('Access_to_Resources:N'),
    alt.value('lightgray')
)


opacity_condition = alt.condition(
    rating_select,
    alt.value(1),  
    alt.value(0)  
)

highlight_ratings = chart.add_params(
    rating_select
).encode(
    color=rating_color_condition,  
    opacity=opacity_condition  
).properties(title="Attendence Vs Exam Scores Segmented By Access To Resources") 


highlight_ratings

alt.Chart(...)